In [1]:
import agentpy as ap  # Library for creating agents
import numpy as np  # NumPy library for numerical operations
import matplotlib.pyplot as plt  # Library for plotting
import seaborn as sns  # Library for statistical data visualization
from random import randint  # For generating random numbers
import IPython  # For displaying videos in the notebook
from matplotlib.animation import FuncAnimation  # For creating animations (used by agentpy)

DIRECTIONS = [(1, -1), (1, 0), (1, 1),  # Possible directions for agent movement
              (0, -1),          (0, 1),
              (-1, -1), (-1, 0), (-1, 1)]



In [2]:
class TestAgent(ap.Agent): # Agent that moves randomly

    def setup(self):
        self.test_id = 1 # Agent ID
        self.type = "test" # Agent type (used when trying to access all agents)
        self.move_count = 0 # Tracks the number of movements

    def move_agent(self):
        # Randomly move the agent
        movement = DIRECTIONS[randint(0, 7)] # Get a random direction
        # To move the agent, you need to access the model it belongs to, then access the grid (which I named "ground", the name MUST be the same),
        # and then use the "move_by" method, which takes the agent and the movement as a tuple (x, y) as arguments
        self.model.ground.move_by(self, movement) 

        self.move_count += 1 # Increase the agent's move count

    def get_agent_id(self):
        return self.test_id # This is somewhat useless because you can access the ID using agent.test_id, but i left it here from when I was testing
    
    def get_position(self):
        return self.model.ground.positions[self]  # Same as above, you can access the position using agent.model.ground.positions[agent]


In [3]:
class TestAgent2(ap.Agent): # Similar to the previous agent, but moves in a staircase pattern either up-right or down-left

    def setup(self):
        self.test_id = 2
        self.type = "test"
        self.move_count = 0
        self.old_position = None # to store the previous position
        self.has_hit_wall = False # to track if it has hit a wall and needs to change direction
        self.movement_pattern = "up_right" # determines the movement pattern

    def move_agent(self):
        # Save the old position for comparison
        self.old_position = self.model.ground.positions[self]

        # Determine the direction based on the movement pattern and move count
        if self.movement_pattern == "up_right":
            # Check if the move count is even or odd to decide whether to move horizontally or vertically
            direction = DIRECTIONS[1] if self.move_count % 2 == 0 else DIRECTIONS[4]
        else:  # down_left pattern
            direction = DIRECTIONS[6] if self.move_count % 2 == 0 else DIRECTIONS[3]

        # Attempt to move the agent
        self.model.ground.move_by(self, direction)
        new_position = self.model.ground.positions[self]

        # Check if the position has changed to determine if it hit a wall
        if new_position == self.old_position: 
            # If it hit a wall, toggle the movement pattern and recurse
            self.toggle_movement_pattern()
            self.move_agent()  # Recursive call to try moving again immediately
            #missing recursive safety check implemented in DiagAgent
        else:
            # Increment move count only if the move was successful
            self.move_count += 1

    def toggle_movement_pattern(self):
        # Toggle the movement pattern between up_right and down_left
        self.movement_pattern = "down_left" if self.movement_pattern == "up_right" else "up_right"

    def get_agent_id(self):
        return self.test_id
    
    def get_position(self):
        return self.model.ground.positions[self]

In [4]:
class DiagAgent(ap.Agent):
    # Agent that moves in a diagonal pattern, in any of the 4 diagonal directions
    def setup(self):
        self.test_id = 3
        
        self.custom_id = ''.join(["{}".format(randint(0, 9)) for num in range(0, 10)]) #randomly generated 10 digit id
        self.type = "test"
        self.old_position = None #again, to store the previous position
        #random direction
        self.direction = self.model.random.choice(["up_right", "down_right", "up_left", "down_left"])
        #every agent moves towards the center
    
                
        # This dictionary now represents the order of movement changes for staircase movement
        self.directions_dict = {
            "up_right": [("right", (1, 0)), ("up", (0, -1))],
            "down_right": [("right", (1, 0)), ("down", (0, 1))],
            "up_left": [("left", (-1, 0)), ("up", (0, -1))],
            "down_left": [("left", (-1, 0)), ("down", (0, 1))]
        }
        self.move_count = 0  # To alternate between horizontal and vertical movement, and to track the number of movements
        self.move_tries = 0  # To prevent infinite loops, limit to 4 tries (4 directions to try)

    def move_agent(self):
        direction_sequence = self.directions_dict[self.direction] # Get the movement sequence based on the current direction
        move_direction = direction_sequence[self.move_count % 2][1]  # Alternates between 0 and 1 (even or odd) to get the next direction, either horizontal or vertical
        
        old_position = self.model.ground.positions[self] # Save the old position for comparison
        self.model.ground.move_by(self, move_direction) # Move the agent with the next direction as a tuple (x, y)
        new_position = self.model.ground.positions[self] # Get the new position

        if old_position == new_position or len(self.model.ground.agents[new_position]) > 1:  # Collision detected if the position hasn't changed or if there are other agents in the new position
            self.change_direction_on_collision() # Change direction based on the collision
            if len(self.model.ground.agents[new_position]) > 1: # Check if the collision was with another agent or a wall
                self.model.agent_collisions += 1
            else:
                self.model.wall_collisions += 1
            if self.move_tries < 4: # Try moving again up to 4 times (4 directions to try), to prevent infinite loops
                self.move_tries += 1 # Increment the number of tries
                self.move_agent()  # Try moving again immediately
            
        else:
            self.move_count += 1  # Proceed to next step in movement sequence
        

    def change_direction_on_collision(self):
        # Change direction based on current pattern and collision
        if self.move_count % 2 == 0:  # Horizontal movement caused the collision
            if "right" in self.direction:
                self.direction = self.direction.replace("right", "left")
            else:
                self.direction = self.direction.replace("left", "right")
        else:  # Vertical movement caused the collision
            if "up" in self.direction:
                self.direction = self.direction.replace("up", "down")
            else:
                self.direction = self.direction.replace("down", "up")

        

    def get_agent_id(self):
        return self.test_id
    
    def get_position(self):
        return self.model.ground.positions[self]
    
        

In [5]:
class TestModel(ap.Model):

    def setup(self):
        # Called at the start of the simulation
        self.var = self.p.var # variable I made for testing purposes
        self.agent_3 = ap.AgentList(self, self.p.agent_n, DiagAgent)
        self.agents = [] # list of agents
        self.agents.extend(self.agent_3) # add the agents to the list
        self.agent_positions = [] # list to store the positions of the agents
        self.agent_move_counts = [] # list to store the final move counts of the agents
        for i in range(self.p.agent_n):
            self.agent_positions.append([]) # create an empty list for each agent to store their positions individually
        

        # grid setup
        self.width = self.p.width # get the width and height of the grid
        self.height = self.p.height
        
        # create the grid
        self.ground = ap.Grid(self, (self.width, self.height), track_empty=True, check_border=True)
        
        # IMPORTANT:
        # You have to add each type of agent to the grid separately for some reason, something that the documentation doesn't mention.
        # I tried adding only self.agents, and I spent a while trying to figure out why it didn't work
        # I saw in other activities that you can add multiple agents of the same type (as ive done here), but not of different types
        # If you try, it will only add the first type
        self.ground.add_agents(self.agent_3, random=True, empty=False)
        self.agent_collisions = 0
        self.wall_collisions = 0

        # Set directions of all agents heading towards the center (optional, done to increase the chances of collisions for testing)
        for agent in self.agents:
            if agent.get_position()[0] < self.width / 2: # Check if the agent is on the left or right side
                if agent.get_position()[1] < self.height / 2: # Check if the agent is on the top or bottom side
                    agent.direction = "down_right"
                else:
                    agent.direction = "up_right"
            else:  
                if agent.get_position()[1] < self.height / 2:
                    agent.direction = "down_left"
                else:
                    agent.direction = "up_left"


    def step(self):
        # Called at each step of the simulation
        for agent in self.agents:
            agent.move_tries = 0 # Reset move tries for each agent
            agent.move_agent()
        # pass
        # If you have an empty function, you need to include pass so that it doesn't throw an error

    def update(self):
        # Called after setup and after each step
        for agent in self.agents:
            self.agent_positions[agent.test_id-1].append(agent.get_position())
        # Add the positions of the agents to the positions list in their own index
        
        #print out grid
        print(self.ground.attr_grid('test_id'))
        print()

    def end(self):
        # Called at the end of the simulation

        # The report method is used to store the final value of 'var' in the results
        # You can access this value later with results['reporters']['var']
        self.report('var', self.var)

        # The report method is used to store the final list of 'agents' in the results
        # You can access this list later with results['reporters']['agents']
        self.report('agents', self.agents)

        # The report method is used to store the final list of 'agent_positions' in the results
        # You can access this list later with results['reporters']['agent_positions']
        self.report('agent_positions', self.agent_positions)

        # For each agent, append its move count to the 'agent_move_counts' list
        for agent in self.agents:
            self.agent_move_counts.append(agent.move_count)

        # The report method is used to store the final list of 'agent_move_counts' in the results
        # You can access this list later with results['reporters']['agent_move_counts']
        self.report('agent_move_counts', self.agent_move_counts)

        # The report method is used to store the final value of 'agent_collisions' in the results
        # You can access this value later with results['reporters']['agent_collisions']
        self.report('agent_collisions', self.agent_collisions)

        # The report method is used to store the final value of 'wall_collisions' in the results
        # You can access this value later with results['reporters']['wall_collisions']
        self.report('wall_collisions', self.wall_collisions)

        # Note: The report method should be used properly to ensure that the data is stored correctly
        # and can be accessed later when you want to analyze or plot it



In [6]:
parameters = {
    'var': 1,
    'steps':200, #aunq no lo menciones en el modelo, tienes q ponerlo en los parametros pq ya lo lee x default
    'width': 20,
    'height': 20,
    "agent_n": 20
}

model = TestModel(parameters) #crea el modelo

results = model.run() #corre el modelo

[[nan nan nan nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan  3. nan nan nan nan nan nan nan  3. nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan  3. nan nan nan nan nan nan nan nan
   3. nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [ 3. nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [ 3. nan nan  3. nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan  3. nan

In [7]:
#You can access the values directly from the model as seen below
print (" values from the model directly\n")
print ("var = ", model.var)
print ("agents = ", len(model.agents)) # Print the number of agents

# You can also access the values from the results dictionary declared in the end method

print("\nvalues from the results dictionary\n")
print("results dictionary = \n", results)
# Print the 'info' dictionary
print("results dictionary info = \n", results['info'])

# Print the 'reporters' dictionary
print("reporters dictionary = \n", results['reporters'])

# Print the columns of the 'reporters' dictionary
print("reporters dictionary columns = \n", results['reporters'].columns)

# Print the 'var' value info
print("var = ", results['reporters']['var'], "\n")  # since its stored as a pandas series

# Print the 'var' value itself
print("var (method 1)= ", results['reporters']['var'][0], "\n") # returns the first value of the series
#or
print("var (method 2)= ", results['reporters']['var'].values, "\n") # returns the series as a numpy array

# Print the agent move counts
print("agent_move_counts = ", results['reporters']['agent_move_counts'])


 values from the model directly

var =  1
agents =  20

values from the results dictionary

results dictionary = 
 DataDict {
'info': Dictionary with 9 keys
'parameters': 
    'constants': Dictionary with 5 keys
'reporters': DataFrame with 7 variables and 1 row
}
results dictionary info = 
 {'model_type': 'TestModel', 'time_stamp': '2024-03-03 20:29:13', 'agentpy_version': '0.1.6.dev0', 'python_version': '3.9.6', 'experiment': False, 'completed': True, 'created_objects': 21, 'completed_steps': 200, 'run_time': '0:00:00.435717'}
reporters dictionary = 
                                      seed  var  \
0  66910266178514810233087313852472286714    1   

                                              agents  \
0  [test (Obj 1), test (Obj 2), test (Obj 3), tes...   

                                     agent_positions  \
0  [[], [], [(1, 1), (16, 1), (0, 6), (10, 6), (1...   

                                   agent_move_counts  agent_collisions  \
0  [200, 200, 200, 200, 200, 200, 200, 2

In [8]:
# agentpy comes with two built-in functions, animate() and gridplot(), which simplify matplotlib operations.
# First, you need to define your own function that sets up the plot. Here, I created `animation_plot`, which takes the model and the ax (I still don't know what ax is).

def animation_plot(model, ax):
    # The `attr_grid` function retrieves the grid and takes an attribute to search for within each agent or cell. In my case, I pass the `test_id` attribute of each agent.
    # Each time it runs, it returns a numpy matrix of the entire grid. If a cell is empty, it writes NaN, if I remember correctly.
    # But when it finds an agent, it writes the value of the attribute passed, in my case, the `test_id` of the agent in that cell.
    # The only thing is that since it's a discrete space, there can only be one value per cell. But they mention that in the documentation.
    attr_grid = model.ground.attr_grid('test_id')
    # Based on the values in the `attr_grid`, you can create a color dictionary based on the keys. By default, if you set None, that color will be applied to the NaN cells.
    color_dict = {1: 'red', 2: 'blue', 3: 'green', None: 'white'}
    # Finally, you can use the `gridplot` function. For some reason, if I passed the `color_dict`, I had to set `convert=True`, so keep that in mind.
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    # You can then add regular matplotlib operations, such as setting the title or labels.
    ax.set_title(f"test model step {model.t}\n"
                 f"Agent collisions: {model.agent_collisions}\n"
                f"Wall collisions: {model.wall_collisions}")

# You need to create a figure and axes for matplotlib.
fig, ax = plt.subplots()

# Then, you can create the animation. It takes the model, the figure, the axes, and the custom plot function you defined above.
model = TestModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)


[[nan nan  3. nan nan nan nan nan nan  3. nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan  3. nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan  3. nan nan nan nan nan nan nan nan  3.
  nan nan]
 [ 3. nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan  3. nan nan nan  3. nan nan nan nan nan nan  3. nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan  3. nan nan  3. nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan

In [9]:
#and you render the animation using the display function from IPython
#this method only works in jupyter notebooks, if you want to run it in a script you have to use other methods
IPython.display.HTML(animation.to_jshtml(fps=15))

[[nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan  3. nan nan nan nan nan nan  3. nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan  3. nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan  3. nan nan nan nan nan nan nan nan  3.
  nan nan]
 [ 3. nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan  3. nan nan nan  3. nan nan nan nan nan nan  3. nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan  3. nan nan  3. nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan  3. nan nan

[[nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan  3. nan nan nan nan nan nan  3. nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan  3. nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan  3. nan nan nan nan nan nan  3. nan
  nan nan]
 [nan  3. nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan  3. nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan  3. nan nan nan  3. nan nan nan nan  3. nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan  3. nan nan  3. nan nan nan nan nan nan nan nan nan
  nan nan]
 [nan nan nan nan nan nan nan nan nan nan nan nan  3. nan nan nan